In [ ]:
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
class cvg:
    def __init__(self, attributes, ground_truth, n_test=2, order_dim=0):
        self._order        = order_dim
        self._ntests       = n_test
        self._actual_ntest = 0
        self._size         = attributes.shape[order_dim]
        self._att          = attributes
        self._gt           = ground_truth
        
        if attributes.shape[0] != ground_truth.shape[0] or \
           attributes.shape[1] != ground_truth.shape[1] :
                raise ValueError('attributes and ground_truth must have the same 2D shape')
        
    def __iter__(self):
        return self
    
    def __next__(self):
        if self._actual_ntest == self._ntests:
            raise StopIteration
        
        step = self._size / self._ntests
        train_filter = (np.arange(self._size) - step * self._actual_ntest) % self._size < step
        
        if self._order == 0:
            Xtrain = self._att[train_filter].reshape(-1, self._att.shape[2])
            Xtest  = self._att[train_filter == False].reshape(-1, self._att.shape[2])
            Ytrain = self._gt[train_filter].reshape(-1, 1)
            Ytest  = self._gt[train_filter == False].reshape(-1, 1)
        else:
            Xtrain = self._att[:,train_filter].reshape(-1, self._att.shape[2])
            Xtest  = self._att[:,train_filter == False].reshape(-1, self._att.shape[2])
            Ytrain = self._gt[:,train_filter].reshape(-1, 1)
            Ytest  = self._gt[:,train_filter == False].reshape(-1, 1)

        
        self._actual_ntest += 1
        
        return (Xtrain, Xtest, Ytrain, Ytest, train_filter)

In [ ]:
X = np.arange(100*200*10).reshape(100, 200, 10)
Y = np.arange(100 * 200).reshape(100, 200)

for xn, xt, yn, yt, t in cvg(X, Y, 10, 1):
        disp = np.zeros(Y.shape)
        disp[:,t] = 1.
        plt.imshow(disp)
        plt.show()
        


In [ ]:
import sys
sys.path.append('..')
from CrossValidationGenerator import APsCVG
sys.path.append('../triskele/python')
import triskele

In [ ]:
gt = triskele.read('../Data/ground_truth/2018_IEEE_GRSS_DFC_GT_TR.tif')
att = np.array((gt, gt))
att = np.moveaxis(att, 0, 2)

In [ ]:
for xt, xv, yt, yv, ti in APsCVG(gt, att, 1):
    print(xt.shape, yt.shape, xv.shape, yv.shape)
    plt.imshow(ti * 1.)
    plt.show()